# Query Composition Investigation

1. Find an example of query composition in a tiny model. 
2. Show that we can use an SAE to identify the features in the queries

Let's start with tiny stories. 

In [1]:
import sys 
sys.path.append("..")

from importlib import reload

import joseph
from joseph.analysis import *
from joseph.visualisation import *
from joseph.utils import *
from joseph.data import *


reload(joseph.analysis)
reload(joseph.visualisation)
reload(joseph.utils)
reload(joseph.data)

from joseph.analysis import *
from joseph.visualisation import *
from joseph.utils import *
from joseph.data import *

# turn torch grad tracking off
torch.set_grad_enabled(False)


model = HookedTransformer.from_pretrained(
    "tiny-stories-2L-33M",
    # center_unembed=True,
    # center_writing_weights=True,
    # fold_ln=True,
    # refactor_factored_attn_matrices=True,
)
# model.set_use_split_qkv_input(True)
# model.set_use_attn_result(True)
import transformer_lens.evals as evals
evals.sanity_check(model)

/Users/josephbloom/miniforge3/envs/mats_sae_training/lib/python3.11/site-packages/transformers/utils/generic.py:441: UserWarning: torch.utils._pytree._register_pytree_node is deprecated. Please use torch.utils._pytree.register_pytree_node instead.
  _torch_pytree._register_pytree_node(
/Users/josephbloom/miniforge3/envs/mats_sae_training/lib/python3.11/site-packages/transformers/utils/generic.py:309: UserWarning: torch.utils._pytree._register_pytree_node is deprecated. Please use torch.utils._pytree.register_pytree_node instead.
  _torch_pytree._register_pytree_node(
/Users/josephbloom/miniforge3/envs/mats_sae_training/lib/python3.11/site-packages/transformers/utils/generic.py:309: UserWarning: torch.utils._pytree._register_pytree_node is deprecated. Please use torch.utils._pytree.register_pytree_node instead.
  _torch_pytree._register_pytree_node(


Loaded pretrained model tiny-stories-2L-33M into HookedTransformer


tensor(6.5646, device='mps:0')

Looking for multi-token induction head.
- Let's check for induction heads first. 

In [2]:
model.generate(
    "Once upon a time", max_new_tokens=20, stop_at_eos=False
)

  0%|          | 0/20 [00:00<?, ?it/s]

'Once upon a time there were two best friends who liked to tease each other. One was dressed in the most popular uniform'

In [3]:
import pandas as pd
import itertools
import numpy as np

def tensor_to_long_data_frame(tensor_result, dimension_names):
    assert len(tensor_result.shape) == len(
        dimension_names
    ), "The number of dimension names must match the number of dimensions in the tensor"

    tensor_2d = tensor_result.reshape(-1)
    df = pd.DataFrame(tensor_2d.detach().numpy(), columns=["Score"])

    indices = pd.MultiIndex.from_tuples(
        list(np.ndindex(tensor_result.shape)),
        names=dimension_names,
    )
    df.index = indices
    df.reset_index(inplace=True)
    return df

q_composition_scores = model.all_composition_scores(mode = "Q")
q_comp_df = tensor_to_long_data_frame(q_composition_scores.detach().cpu(), ["Layer1", "Head1", "Layer2", "Head2"])
q_comp_df.sort_values("Score", ascending=False).head(10).style.background_gradient(cmap="Blues")

Ok so layer 0 head 6 seems to produce stuff that layer 1 head 11,10,3 all point to. Let's analyse that one. 

In [4]:
def get_webtext(seed: int = 420, dataset="stas/openwebtext-10k", split="train[:1%]") -> List[str]:
    """Get 10,000 sentences from the OpenWebText dataset"""

    # Let's see some WEBTEXT
    train_dataset = load_dataset(dataset, split=split)
    # train_dataset = raw_dataset["train"]
    dataset = [train_dataset[i]["text"] for i in range(len(train_dataset))]

    # Shuffle the dataset (I don't want the Hitler thing being first so use a seeded shuffle)
    np.random.seed(seed)
    np.random.shuffle(dataset)

    return dataset

data = get_webtext(dataset="roneneldan/TinyStories")

In [37]:
path = "checkpoints/399ihu5z/final_sparse_autoencoder_tiny-stories-2L-33M_blocks.1.attn.hook_q_4096.pt"
sparse_autoencoder = SparseAutoencoder.load_from_pretrained(path)

In [38]:
from tqdm import tqdm

str_token_list = []
loss_list = []
ablated_loss_list = []
data = get_webtext(dataset="roneneldan/TinyStories")

import joseph.analysis as analysis
reload(analysis)

NUM_PROMPTS = 100
# MAX_PROMPT_LEN = 100
# BATCH_SIZE = 10
dataframe_list = []
with torch.no_grad():
    for i in tqdm(range(NUM_PROMPTS)):
        
        # Get Token Data
        prompt = data[i]
        # new_str = data[BATCH_SIZE * i: BATCH_SIZE * (i + 1)]
        token_df, _, _= analysis.eval_prompt(prompt, model=model, sparse_autoencoder=sparse_autoencoder)
        token_df["batch"] = i
        token_df["label"] = token_df["batch"].astype(str) + "/" + token_df["pos"].astype(str)
        dataframe_list.append(token_df)
        
df = pd.concat(dataframe_list)

print(df.shape)
print(df.columns)


100%|██████████| 100/100 [00:32<00:00,  3.12it/s]

(21253, 23)
Index(['str_tokens', 'unique_token', 'context', 'batch', 'pos', 'label',
       'loss', 'max_idx_pos', 'max_idx_tok', 'max_idx_tok_value',
       'ablated_loss', 'loss_diff', 'q_norm', 'rec_q_norm', 'mse_loss',
       'explained_variance', 'num_active_features', 'top_k_feature_acts',
       'top_k_features', 'rec_q_max_idx_pos', 'rec_q_max_idx_tok',
       'rec_q_max_idx_tok_value', 'kl_divergence'],
      dtype='object')


In [39]:
df.sort_values("loss_diff", ascending=False).head(10).style.background_gradient(cmap="Blues")

In [7]:
px.scatter(
    df,
    x="max_idx_tok_value",
    y="loss_diff",
    hover_data=["label", "context", "max_idx_tok"],
    marginal_x="histogram",
    marginal_y="histogram",
)

Not clear what the head is doing. Possibly doing some sort of summarization?

In [8]:
px.histogram(df, x="loss_diff", nbins=100, title="Loss difference distribution")

In [9]:
from transformer_lens.utils import test_prompt

LAYER_IDX = 1; HEAD_IDX = 11
HEAD_HOOK_RESULT_NAME = utils.get_act_name("z", LAYER_IDX)
def hook_to_ablate_head(head_output: Float[Tensor, "batch seq_len head_idx d_head"], hook: HookPoint, head = (LAYER_IDX, HEAD_IDX)):
    assert head[0] == hook.layer(), f"{head[0]} != {hook.layer()}"
    assert ("result" in hook.name) or ("q" in hook.name) or ("z" in hook.name)
    head_output[:, :, head[1], :] = 0
    return head_output

batch = 1; pos = 153+1
prompt = data[batch]
print(prompt)
tokens = model.to_tokens(prompt)
loss, original_cache = model.run_with_cache(tokens, return_type="loss", loss_per_token=True)


example_prompt = model.to_string(tokens[:,:pos+1])[0]
example_prompt_answer = model.to_string(tokens[:,pos+1])
test_prompt(example_prompt, example_prompt_answer, model, prepend_bos=False, prepend_space_to_answer=False)

with model.hooks(fwd_hooks=[(HEAD_HOOK_RESULT_NAME, hook_to_ablate_head)]):
    test_prompt(example_prompt, example_prompt_answer, model, prepend_bos=False, prepend_space_to_answer=False)
    logits_reconstructed, cache_reconstructed_res_stream = model.run_with_cache(example_prompt, prepend_bos=False)



Sara and Ben like to play pirates. They have a big box that is their ship. They have hats and swords and a map. The map shows them where to find treasure.

One day, they find a shiny coin in the sand. Sara is happy. She puts the coin in her pocket. Ben is jealous. He wants the coin too. He tries to take it from Sara. They fight.

"Stop!" says Mom. "You have to share. Pirates don't fight with their friends. They work together."

Mom gives them a cloth. She tells them to wipe the coin. It is dirty. They wipe the coin. They see something on it. It is a picture of a star.

"Look!" says Sara. "It is a clue. Maybe it is part of the treasure."

"Maybe you are right," says Ben. "Let's look at the map. Maybe the star is on it."

They look at the map. They see a star. It is near a big tree. They run to the tree. They dig under it. They find a box. It is full of more coins and jewels.

"Wow!" says Sara. "We found the treasure. We are the best pirates ever."

"Yes, we are," says Ben. "And we are t

Performance on answer token:
Rank: 0        Logit: 23.19 Prob: 58.48% Token: | says|

Top 0th token. Logit: 23.19 Prob: 58.48% Token: | says|
Top 1th token. Logit: 22.63 Prob: 33.47% Token: | Mom|
Top 2th token. Logit: 20.38 Prob:  3.50% Token: | said|
Top 3th token. Logit: 19.71 Prob:  1.79% Token: | Sara|
Top 4th token. Logit: 19.10 Prob:  0.98% Token: | she|
Top 5th token. Logit: 19.09 Prob:  0.97% Token: | they|
Top 6th token. Logit: 17.23 Prob:  0.15% Token: | Ben|
Top 7th token. Logit: 16.82 Prob:  0.10% Token: | They|
Top 8th token. Logit: 16.78 Prob:  0.10% Token: | the|
Top 9th token. Logit: 16.71 Prob:  0.09% Token: | say|


Ranks of the answer tokens: [(' says', 0)]

Tokenized prompt: ['<|endoftext|>', 'S', 'ara', ' and', ' Ben', ' like', ' to', ' play', ' pirates', '.', ' They', ' have', ' a', ' big', ' box', ' that', ' is', ' their', ' ship', '.', ' They', ' have', ' hats', ' and', ' swords', ' and', ' a', ' map', '.', ' The', ' map', ' shows', ' them', ' where', ' to', ' find', ' treasure', '.', '\n', '\n', 'One', ' day', ',', ' they', ' find', ' a', ' shiny', ' coin', ' in', ' the', ' sand', '.', ' Sara', ' is', ' happy', '.', ' She', ' puts', ' the', ' coin', ' in', ' her', ' pocket', '.', ' Ben', ' is', ' jealous', '.', ' He', ' wants', ' the', ' coin', ' too', '.', ' He', ' tries', ' to', ' take', ' it', ' from', ' Sara', '.', ' They', ' fight', '.', '\n', '\n', '"', 'Stop', '!"', ' says', ' Mom', '.', ' "', 'You', ' have', ' to', ' share', '.', ' Pirates', ' don', "'t", ' fight', ' with', ' their', ' friends', '.', ' They', ' work', ' together', '."', '\n', '\n', 'Mom', ' gives', ' them', ' a', ' cloth', '.', ' She', ' tells', ' them', ' to

Performance on answer token:
Rank: 3        Logit: 20.10 Prob:  4.19% Token: | says|

Top 0th token. Logit: 22.80 Prob: 61.99% Token: | Mom|
Top 1th token. Logit: 21.55 Prob: 17.72% Token: | Sara|
Top 2th token. Logit: 21.06 Prob: 10.92% Token: | said|
Top 3th token. Logit: 20.10 Prob:  4.19% Token: | says|
Top 4th token. Logit: 19.28 Prob:  1.84% Token: | she|
Top 5th token. Logit: 18.76 Prob:  1.10% Token: | Ben|
Top 6th token. Logit: 18.47 Prob:  0.82% Token: | they|
Top 7th token. Logit: 16.92 Prob:  0.17% Token: | the|
Top 8th token. Logit: 16.82 Prob:  0.16% Token: | Tim|
Top 9th token. Logit: 16.50 Prob:  0.11% Token: | a|


Ranks of the answer tokens: [(' says', 3)]

In [10]:
# from circuitsvis.attention import attention_patterns
logits, cache = model.run_with_cache(example_prompt, prepend_bos=False)
patterns = cache[f"blocks.{LAYER_IDX}.attn.hook_pattern"][0,HEAD_IDX].detach().cpu()
# attention_patterns(tokens=model.to_str_tokens(test_prompt, prepend_bos=False), attention=patterns)
token_df = make_token_df(model, tokens[:,:pos+1])
token_df["attn"] = patterns[-1,:]
# patterns = patterns.unsqueeze(0).repeat(2,1,1)
# plot_attn(patterns, token_df)
token_df.sort_values("attn", ascending=False).head(10).style.background_gradient(cmap="Blues")

- Example 1: This head was responsible for inhibiting !" and without this it is predict confidently. 
- Example 2: This head was responsible for increasing "."
- Example 3: This head was responsbile for inhibiting ",", because "Jane" is the next token and it's attending to "Jane" and "She"

Theory: The head deals with some features relating to punctuation.

Current hypothesis is that it's doing a bunch of stuff. 
- checking whether the sentence is over.

# Copy Suppression Analysis

## Load in Example

In [13]:

batch = 1; pos = 154
prompt = data[batch]
tokens = model.to_tokens(prompt)
loss, original_cache = model.run_with_cache(tokens, return_type="loss", loss_per_token=True)

example_prompt = model.to_string(tokens[:,:pos+1])[0]
example_prompt_answer = model.to_string(tokens[:,pos+1])
example_prompt_tokens = tokens[:,:pos+1]
_, cache_original = model.run_with_cache(example_prompt_tokens, prepend_bos=False)


def test_prompt_with_sae(example_prompt, example_prompt_answer, model, sparse_autoencoder, cache_original):
    
    model.reset_hooks()
    utils.test_prompt(example_prompt, example_prompt_answer, model, prepend_space_to_answer=False, prepend_bos=False)

    with model.hooks(fwd_hooks=[(HEAD_HOOK_RESULT_NAME, hook_to_ablate_head)]):
        utils.test_prompt(example_prompt, example_prompt_answer, model, prepend_bos=False, prepend_space_to_answer=False)

    sae_out, feature_acts, loss, mse_loss, l1_loss = sparse_autoencoder(
        cache_original[sparse_autoencoder.cfg.hook_point][0,HEAD_IDX]
    )
    def reconstr_query_hook(hook_in, hook, reconstructed_query=sae_out, head = HEAD_IDX):
        hook_in[:, head, :] = reconstructed_query
        return hook_in

    with model.hooks(fwd_hooks=[(sparse_autoencoder.cfg.hook_point, reconstr_query_hook)]):
        utils.test_prompt(example_prompt, example_prompt_answer, model,  prepend_bos=False, prepend_space_to_answer=False)
        
    
test_prompt_with_sae(example_prompt, example_prompt_answer, model, sparse_autoencoder, prepend_bos=False, prepend_space_to_answer=False)

Tokenized prompt: ['<|endoftext|>', 'S', 'ara', ' and', ' Ben', ' like', ' to', ' play', ' pirates', '.', ' They', ' have', ' a', ' big', ' box', ' that', ' is', ' their', ' ship', '.', ' They', ' have', ' hats', ' and', ' swords', ' and', ' a', ' map', '.', ' The', ' map', ' shows', ' them', ' where', ' to', ' find', ' treasure', '.', '\n', '\n', 'One', ' day', ',', ' they', ' find', ' a', ' shiny', ' coin', ' in', ' the', ' sand', '.', ' Sara', ' is', ' happy', '.', ' She', ' puts', ' the', ' coin', ' in', ' her', ' pocket', '.', ' Ben', ' is', ' jealous', '.', ' He', ' wants', ' the', ' coin', ' too', '.', ' He', ' tries', ' to', ' take', ' it', ' from', ' Sara', '.', ' They', ' fight', '.', '\n', '\n', '"', 'Stop', '!"', ' says', ' Mom', '.', ' "', 'You', ' have', ' to', ' share', '.', ' Pirates', ' don', "'t", ' fight', ' with', ' their', ' friends', '.', ' They', ' work', ' together', '."', '\n', '\n', 'Mom', ' gives', ' them', ' a', ' cloth', '.', ' She', ' tells', ' them', ' to

Performance on answer token:
Rank: 0        Logit: 23.19 Prob: 58.48% Token: | says|

Top 0th token. Logit: 23.19 Prob: 58.48% Token: | says|
Top 1th token. Logit: 22.63 Prob: 33.47% Token: | Mom|
Top 2th token. Logit: 20.38 Prob:  3.50% Token: | said|
Top 3th token. Logit: 19.71 Prob:  1.79% Token: | Sara|
Top 4th token. Logit: 19.10 Prob:  0.98% Token: | she|
Top 5th token. Logit: 19.09 Prob:  0.97% Token: | they|
Top 6th token. Logit: 17.23 Prob:  0.15% Token: | Ben|
Top 7th token. Logit: 16.82 Prob:  0.10% Token: | They|
Top 8th token. Logit: 16.78 Prob:  0.10% Token: | the|
Top 9th token. Logit: 16.71 Prob:  0.09% Token: | say|


Ranks of the answer tokens: [(' says', 0)]

Tokenized prompt: ['<|endoftext|>', 'S', 'ara', ' and', ' Ben', ' like', ' to', ' play', ' pirates', '.', ' They', ' have', ' a', ' big', ' box', ' that', ' is', ' their', ' ship', '.', ' They', ' have', ' hats', ' and', ' swords', ' and', ' a', ' map', '.', ' The', ' map', ' shows', ' them', ' where', ' to', ' find', ' treasure', '.', '\n', '\n', 'One', ' day', ',', ' they', ' find', ' a', ' shiny', ' coin', ' in', ' the', ' sand', '.', ' Sara', ' is', ' happy', '.', ' She', ' puts', ' the', ' coin', ' in', ' her', ' pocket', '.', ' Ben', ' is', ' jealous', '.', ' He', ' wants', ' the', ' coin', ' too', '.', ' He', ' tries', ' to', ' take', ' it', ' from', ' Sara', '.', ' They', ' fight', '.', '\n', '\n', '"', 'Stop', '!"', ' says', ' Mom', '.', ' "', 'You', ' have', ' to', ' share', '.', ' Pirates', ' don', "'t", ' fight', ' with', ' their', ' friends', '.', ' They', ' work', ' together', '."', '\n', '\n', 'Mom', ' gives', ' them', ' a', ' cloth', '.', ' She', ' tells', ' them', ' to

...

Ranks of the answer tokens: [(' says', 3)]

Tokenized prompt: ['<|endoftext|>', 'S', 'ara', ' and', ' Ben', ' like', ' to', ' play', ' pirates', '.', ' They', ' have', ' a', ' big', ' box', ' that', ' is', ' their', ' ship', '.', ' They', ' have', ' hats', ' and', ' swords', ' and', ' a', ' map', '.', ' The', ' map', ' shows', ' them', ' where', ' to', ' find', ' treasure', '.', '\n', '\n', 'One', ' day', ',', ' they', ' find', ' a', ' shiny', ' coin', ' in', ' the', ' sand', '.', ' Sara', ' is', ' happy', '.', ' She', ' puts', ' the', ' coin', ' in', ' her', ' pocket', '.', ' Ben', ' is', ' jealous', '.', ' He', ' wants', ' the', ' coin', ' too', '.', ' He', ' tries', ' to', ' take', ' it', ' from', ' Sara', '.', ' They', ' fight', '.', '\n', '\n', '"', 'Stop', '!"', ' says', ' Mom', '.', ' "', 'You', ' have', ' to', ' share', '.', ' Pirates', ' don', "'t", ' fight', ' with', ' their', ' friends', '.', ' They', ' work', ' together', '."', '\n', '\n', 'Mom', ' gives', ' them', ' a', ' cloth', '.', ' She', ' tells', ' them', ' to

Performance on answer token:
Rank: 0        Logit: 23.19 Prob: 58.48% Token: | says|

Top 0th token. Logit: 23.19 Prob: 58.48% Token: | says|
Top 1th token. Logit: 22.63 Prob: 33.47% Token: | Mom|
Top 2th token. Logit: 20.38 Prob:  3.50% Token: | said|
Top 3th token. Logit: 19.71 Prob:  1.79% Token: | Sara|
Top 4th token. Logit: 19.10 Prob:  0.98% Token: | she|
Top 5th token. Logit: 19.09 Prob:  0.97% Token: | they|
Top 6th token. Logit: 17.23 Prob:  0.15% Token: | Ben|
Top 7th token. Logit: 16.82 Prob:  0.10% Token: | They|
Top 8th token. Logit: 16.78 Prob:  0.10% Token: | the|
Top 9th token. Logit: 16.71 Prob:  0.09% Token: | say|


Ranks of the answer tokens: [(' says', 0)]

In [14]:
token_df, original_cache, cache_reconstructed_query = eval_prompt([example_prompt], model, sparse_autoencoder)
print(token_df.columns)
filter_cols = ["str_tokens", "unique_token", "context", "batch", "pos", "label", "loss", "loss_diff", 
               "mse_loss", "num_active_features", "max_idx_tok", "max_idx_tok_value", "rec_q_max_idx_tok", "rec_q_max_idx_tok_value",
               "explained_variance", "kl_divergence", "top_k_features"]
token_df[filter_cols].tail(15).style.background_gradient(
    subset=["loss_diff", "mse_loss","explained_variance", "num_active_features", "kl_divergence"],
    cmap="coolwarm")

Index(['str_tokens', 'unique_token', 'context', 'batch', 'pos', 'label',
       'loss', 'max_idx_pos', 'max_idx_tok', 'max_idx_tok_value',
       'ablated_loss', 'loss_diff', 'q_norm', 'rec_q_norm', 'mse_loss',
       'explained_variance', 'num_active_features', 'top_k_feature_acts',
       'top_k_features', 'rec_q_max_idx_pos', 'rec_q_max_idx_tok',
       'rec_q_max_idx_tok_value', 'kl_divergence'],
      dtype='object')


In [15]:
patterns = original_cache[f"blocks.{LAYER_IDX}.attn.hook_pattern"][0,HEAD_IDX].detach().cpu()
token_df_attn = make_token_df(model, example_prompt_tokens)
token_df_attn["original_attn"] = patterns[pos,:pos+1]
patterns = cache_reconstructed_query[f"blocks.{LAYER_IDX}.attn.hook_pattern"][0,HEAD_IDX].detach().cpu()
token_df_attn["reconstructed_attn"] = patterns[pos,:pos+1]
px.line(token_df_attn, y=["original_attn","reconstructed_attn"], hover_name="str_tokens", hover_data=["pos", "batch", "label"], title="Original vs Reconstructed attention").show()
token_df_attn.sort_values("original_attn", ascending=False).head(10).style.background_gradient(cmap="Blues")

## Get top 10 Tokens in the Unembed

In [16]:

example_prompt_tokens = tokens[:,:pos+1]
example_prompt = model.to_string(tokens[:,:pos+1])[0]
example_prompt_answer = model.to_string(tokens[:,pos+1])

logits_original, cache_original = model.run_with_cache(example_prompt_tokens, prepend_bos=False)
# test_prompt_with_sae(example_prompt, example_prompt_answer, model, sparse_autoencoder, prepend_bos=False, prepend_space_to_answer=False)

In [17]:
# def get_logit_scores_df(logit_scores, top_n_tokens=20):
#     vocab_scores, vocab_inds = torch.topk(logit_scores.detach().cpu(), top_n_tokens)
#     tmp = pd.DataFrame({"token": model.to_str_tokens(vocab_inds.int()), "score": vocab_scores}).sort_values("score", ascending=True)
    
#     return tmp
#     # fig = px.bar(tmp, y = "token", x = "score", orientation="h", title="Top 10 vocab scores for last token")
#     # # fonts much larger
#     # fig.update_layout(title_font_size=24, font_size=16, width=600)
#     # fig.show()

# df_original = get_logit_scores_df(logits_original[0,-1,:])
# df_ablation = get_logit_scores_df(logits_ablation[0,-1,:])
# df_reconstructed = get_logit_scores_df(logits_reconstructed[0,-1,:])

# # merge them 
# df_original["type"] = "original"
# df_ablation["type"] = "ablation"
# df_reconstructed["type"] = "reconstructed"
# df = pd.concat([df_original, df_ablation])
# df


# wide_df =  df.pivot(index="token", columns="type", values="score").sort_values("original", ascending=False)
# wide_df["diff"] = wide_df["original"] - wide_df["ablation"]
# wide_df = wide_df.sort_values("diff", ascending=False).head(10)
# wide_df.style.background_gradient(cmap="RdBu", subset=["diff"]) # the head is dropping the logits of a bunch of tokens.

In [18]:
# # lets check if this is direct.
# decomp, labels = cache.get_full_resid_decomposition(return_labels=True, mlp_input=True, layer=LAYER_IDX, expand_neurons=False)
# # get the decomp which matches label "L1H11"
# decomp = decomp[labels.index("L1H11")][0,-1]
# effect_on_logits = decomp @ model.W_U
# effect_on_logits = get_logit_scores_df(effect_on_logits,50257)
# effect_on_logits["rank"]= effect_on_logits["score"].rank(ascending=False)
# # display(effect_on_logits.sort_values("score", ascending=True).head(20).style.background_gradient(cmap="Blues"))
# wide_df = wide_df.join(effect_on_logits.set_index("token"))#.style.background_gradient(cmap="RdBu", subset=["score", "diff", "rank"])
# px.scatter(wide_df, x="score", y="diff", hover_name=wide_df.index, hover_data=["rank"], title="Effect on logits vs original score")

So the effect of the head is not direct! This means that my prior on "the real thing a head is doing is not evident through the unembed projection alone" has been updated up. We should look at another example though, this may be an exception.

## Understanding Features:

So far we've found examples of where the head is important and looked at the features firing, attention pattern and direct/indirect effects of ablating the head on token probabilities. 

However, we'd like to decompose the direct and indirect effects into features individually, rather than as a group.



In [19]:
batch = 1; pos = 154
prompt = data[batch]
tokens = model.to_tokens(prompt)
example_prompt = model.to_string(tokens[:,:pos+1])[0]
example_prompt_answer = model.to_string(tokens[:,pos+1])
example_prompt_tokens = tokens[:,:pos+1]
_, cache_original = model.run_with_cache(tokens[:,:pos+1], prepend_bos=False)

model.reset_hooks()
token_df, original_cache, cache_reconstructed_query = eval_prompt([example_prompt], model, sparse_autoencoder)
print(token_df.columns)
filter_cols = ["str_tokens", "unique_token", "context", "batch", "pos", "label", "loss", "loss_diff", 
               "mse_loss", "num_active_features", "max_idx_tok", "max_idx_tok_value", "rec_q_max_idx_tok", "rec_q_max_idx_tok_value",
               "explained_variance", "kl_divergence", "top_k_features"]
token_df[filter_cols].tail(15).style.background_gradient(
    subset=["loss_diff", "mse_loss", "num_active_features", "kl_divergence"],
    cmap="coolwarm")



Index(['str_tokens', 'unique_token', 'context', 'batch', 'pos', 'label',
       'loss', 'max_idx_pos', 'max_idx_tok', 'max_idx_tok_value',
       'ablated_loss', 'loss_diff', 'q_norm', 'rec_q_norm', 'mse_loss',
       'explained_variance', 'num_active_features', 'top_k_feature_acts',
       'top_k_features', 'rec_q_max_idx_pos', 'rec_q_max_idx_tok',
       'rec_q_max_idx_tok_value', 'kl_divergence'],
      dtype='object')


In [158]:
original_acts = original_cache[sparse_autoencoder.cfg.hook_point]
print(original_acts.shape)
sae_out, feature_acts, loss, mse_loss, l1_loss = sparse_autoencoder(
    original_cache[sparse_autoencoder.cfg.hook_point][:,-1,HEAD_IDX]
)
print(feature_acts.shape)
plot_line_with_top_10_labels(feature_acts[0])


torch.Size([1, 156, 16, 64])
torch.Size([1, 4096])


In [20]:
example_prompt

'<|endoftext|>Sara and Ben like to play pirates. They have a big box that is their ship. They have hats and swords and a map. The map shows them where to find treasure.\n\nOne day, they find a shiny coin in the sand. Sara is happy. She puts the coin in her pocket. Ben is jealous. He wants the coin too. He tries to take it from Sara. They fight.\n\n"Stop!" says Mom. "You have to share. Pirates don\'t fight with their friends. They work together."\n\nMom gives them a cloth. She tells them to wipe the coin. It is dirty. They wipe the coin. They see something on it. It is a picture of a star.\n\n"Look!"'

In [26]:
example_prompt

'<|endoftext|>Sara and Ben like to play pirates. They have a big box that is their ship. They have hats and swords and a map. The map shows them where to find treasure.\n\nOne day, they find a shiny coin in the sand. Sara is happy. She puts the coin in her pocket. Ben is jealous. He wants the coin too. He tries to take it from Sara. They fight.\n\n"Stop!" says Mom. "You have to share. Pirates don\'t fight with their friends. They work together."\n\nMom gives them a cloth. She tells them to wipe the coin. It is dirty. They wipe the coin. They see something on it. It is a picture of a star.\n\n"Look!"'

In [35]:
def test_get_attn_sae_feature_removal(example_prompt, 
                                      example_prompt_answer, 
                                      model, 
                                      sparse_autoencoder,
                                      features_to_remove=[0]):
    
    token_df, original_cache, cache_reconstructed_query = eval_prompt([example_prompt], model, sparse_autoencoder)

    original_acts = original_cache[sparse_autoencoder.cfg.hook_point]
    sae_out, feature_acts, loss, mse_loss, l1_loss = sparse_autoencoder(
       original_acts[0,:,HEAD_IDX]
    )
    
    print(feature_acts.shape)

    def remove_feature_hook(hook_in, hook, head = HEAD_IDX, features_to_remove = features_to_remove):
        print(hook_in.shape)
        for feature_to_remove in features_to_remove:
            feature_dir = feature_acts[-1,feature_to_remove]*sparse_autoencoder.W_dec[feature_to_remove]
            hook_in[:, :, head] -= feature_dir
        return hook_in
    
    with model.hooks(fwd_hooks=[(sparse_autoencoder.cfg.hook_point, remove_feature_hook)]):
        _, cache_removed_feature = model.run_with_cache(tokens, return_type="loss", loss_per_token=True)

    patterns = original_cache[f"blocks.{LAYER_IDX}.attn.hook_pattern"][0,HEAD_IDX].detach().cpu()
    attn_df = make_token_df(model, example_prompt_tokens)
    attn_df["original_attn"] = patterns[pos,:pos+1]
    patterns = cache_reconstructed_query[f"blocks.{LAYER_IDX}.attn.hook_pattern"][0,HEAD_IDX].detach().cpu()
    attn_df["reconstructed_attn"] = patterns[pos,:pos+1]
    patterns = cache_removed_feature[f"blocks.{LAYER_IDX}.attn.hook_pattern"][0,HEAD_IDX].detach().cpu()
    attn_df["ablated_feature_attn"] = patterns[pos,:pos+1]
    fig = px.line(attn_df, 
                  y=["original_attn","reconstructed_attn", "ablated_feature_attn"], 
                  hover_name="str_tokens", 
                  hover_data=["pos", "batch", "label"], 
                  title="Original vs Reconstructed attention")
    
    fig.show()

def test_prompt_with_sae_feature_removal(example_prompt, example_prompt_answer, model, sparse_autoencoder, features_to_remove=[0]):
    
    model.reset_hooks()
    utils.test_prompt(example_prompt, example_prompt_answer, model, prepend_space_to_answer=False, prepend_bos=False)

    with model.hooks(fwd_hooks=[(HEAD_HOOK_RESULT_NAME, hook_to_ablate_head)]):
        utils.test_prompt(example_prompt, example_prompt_answer, model, prepend_bos=False, prepend_space_to_answer=False)

    token_df, original_cache, cache_reconstructed_query = eval_prompt([example_prompt], model, sparse_autoencoder)
    sae_out, feature_acts, loss, mse_loss, l1_loss = sparse_autoencoder(
        original_cache[sparse_autoencoder.cfg.hook_point][0,HEAD_IDX]
    )
    def reconstr_query_hook(hook_in, hook, reconstructed_query=sae_out, head = HEAD_IDX):
        hook_in[:, head, :] = reconstructed_query
        return hook_in

    def remove_feature_hook(hook_in, hook, head = HEAD_IDX, features_to_remove = features_to_remove):
        print(hook_in.shape)
        for feature_to_remove in features_to_remove:
            feature_dir = feature_acts[-1,feature_to_remove]*sparse_autoencoder.W_dec[feature_to_remove]
            hook_in[:, :, head] -= feature_dir
        return hook_in
    
    print("FEATURE REMOVED")
    with model.hooks(fwd_hooks=[(sparse_autoencoder.cfg.hook_point, remove_feature_hook)]):
        utils.test_prompt(example_prompt, example_prompt_answer, model,  prepend_bos=False, prepend_space_to_answer=False)


test_get_attn_sae_feature_removal(
    example_prompt, 
    example_prompt_answer, model, 
    sparse_autoencoder, features_to_remove=[1669, 3489])

test_prompt_with_sae_feature_removal(
    example_prompt, 
    example_prompt_answer, model, 
    sparse_autoencoder, features_to_remove=[1669, 3489])


torch.Size([156, 4096])
torch.Size([1, 346, 16, 64])


Tokenized prompt: ['<|endoftext|>', 'S', 'ara', ' and', ' Ben', ' like', ' to', ' play', ' pirates', '.', ' They', ' have', ' a', ' big', ' box', ' that', ' is', ' their', ' ship', '.', ' They', ' have', ' hats', ' and', ' swords', ' and', ' a', ' map', '.', ' The', ' map', ' shows', ' them', ' where', ' to', ' find', ' treasure', '.', '\n', '\n', 'One', ' day', ',', ' they', ' find', ' a', ' shiny', ' coin', ' in', ' the', ' sand', '.', ' Sara', ' is', ' happy', '.', ' She', ' puts', ' the', ' coin', ' in', ' her', ' pocket', '.', ' Ben', ' is', ' jealous', '.', ' He', ' wants', ' the', ' coin', ' too', '.', ' He', ' tries', ' to', ' take', ' it', ' from', ' Sara', '.', ' They', ' fight', '.', '\n', '\n', '"', 'Stop', '!"', ' says', ' Mom', '.', ' "', 'You', ' have', ' to', ' share', '.', ' Pirates', ' don', "'t", ' fight', ' with', ' their', ' friends', '.', ' They', ' work', ' together', '."', '\n', '\n', 'Mom', ' gives', ' them', ' a', ' cloth', '.', ' She', ' tells', ' them', ' to

Performance on answer token:
Rank: 0        Logit: 23.19 Prob: 58.48% Token: | says|

Top 0th token. Logit: 23.19 Prob: 58.48% Token: | says|
Top 1th token. Logit: 22.63 Prob: 33.47% Token: | Mom|
Top 2th token. Logit: 20.38 Prob:  3.50% Token: | said|
Top 3th token. Logit: 19.71 Prob:  1.79% Token: | Sara|
Top 4th token. Logit: 19.10 Prob:  0.98% Token: | she|
Top 5th token. Logit: 19.09 Prob:  0.97% Token: | they|
Top 6th token. Logit: 17.23 Prob:  0.15% Token: | Ben|
Top 7th token. Logit: 16.82 Prob:  0.10% Token: | They|
Top 8th token. Logit: 16.78 Prob:  0.10% Token: | the|
Top 9th token. Logit: 16.71 Prob:  0.09% Token: | say|


Ranks of the answer tokens: [(' says', 0)]

...

Ranks of the answer tokens: [(' says', 3)]

FEATURE REMOVED
Tokenized prompt: ['<|endoftext|>', 'S', 'ara', ' and', ' Ben', ' like', ' to', ' play', ' pirates', '.', ' They', ' have', ' a', ' big', ' box', ' that', ' is', ' their', ' ship', '.', ' They', ' have', ' hats', ' and', ' swords', ' and', ' a', ' map', '.', ' The', ' map', ' shows', ' them', ' where', ' to', ' find', ' treasure', '.', '\n', '\n', 'One', ' day', ',', ' they', ' find', ' a', ' shiny', ' coin', ' in', ' the', ' sand', '.', ' Sara', ' is', ' happy', '.', ' She', ' puts', ' the', ' coin', ' in', ' her', ' pocket', '.', ' Ben', ' is', ' jealous', '.', ' He', ' wants', ' the', ' coin', ' too', '.', ' He', ' tries', ' to', ' take', ' it', ' from', ' Sara', '.', ' They', ' fight', '.', '\n', '\n', '"', 'Stop', '!"', ' says', ' Mom', '.', ' "', 'You', ' have', ' to', ' share', '.', ' Pirates', ' don', "'t", ' fight', ' with', ' their', ' friends', '.', ' They', ' work', ' together', '."', '\n', '\n', 'Mom', ' gives', ' them', ' a', ' cloth', '.', ' She', ' tells

Performance on answer token:
Rank: 0        Logit: 23.19 Prob: 58.48% Token: | says|

Top 0th token. Logit: 23.19 Prob: 58.48% Token: | says|
Top 1th token. Logit: 22.63 Prob: 33.47% Token: | Mom|
Top 2th token. Logit: 20.38 Prob:  3.50% Token: | said|
Top 3th token. Logit: 19.71 Prob:  1.79% Token: | Sara|
Top 4th token. Logit: 19.10 Prob:  0.98% Token: | she|
Top 5th token. Logit: 19.09 Prob:  0.97% Token: | they|
Top 6th token. Logit: 17.23 Prob:  0.15% Token: | Ben|
Top 7th token. Logit: 16.82 Prob:  0.10% Token: | They|
Top 8th token. Logit: 16.78 Prob:  0.10% Token: | the|
Top 9th token. Logit: 16.71 Prob:  0.09% Token: | say|


Ranks of the answer tokens: [(' says', 0)]

Seems like we have two features that for on ." ," !" (ends of speech quotes) and they are causally responsible for attention to "says". We can look at examples of where the feature fires and see if it always attends to the same token.

One idea is to use virtual weights. Another would be to look for examples of the feature firing

## Dynamic Analysis of Features:

In [86]:
tmp = df[df.top_k_features.apply(lambda x: (3489 in x) and (1669 in x))].head(30)

: 

In [51]:
print(df[df.top_k_features.apply(lambda x: 1669 in x)].shape[0])
print(df[df.top_k_features.apply(lambda x: 3489 in x)].shape[0])
print(df[df.top_k_features.apply(lambda x: (1669 in x) and (3489 not in x))].shape[0])
print(df[df.top_k_features.apply(lambda x: (1669 not in x) and (3489 in x))].shape[0])

146
157
37
48


In [44]:
tmp = df[df.top_k_features.apply(lambda x: 1669 in x)].head(30)
tmp[[]]

str_tokens unique_token                           context  batch  pos  \
88          !"        !"/88               .\n\n"Stop|!"| says      1   88   
153         !"       !"/153               .\n\n"Look|!"| says      1  153   
156          .        ./156            "Look!" says Sara|.| "      1  156   
170         ."       ."/170     is part of the treasure|."|\n      1  170   
178         ,"       ,"/178     "Maybe you are right|,"| says      1  178   
196         ."       ."/196           the star is on it|."|\n      1  196   
246         !"       !"/246                .\n\n"Wow|!"| says      1  246   
262         ."       ."/262   are the best pirates ever|."|\n      1  262   
268         we       we/268                \n\n"Yes,| we| are      1  268   
270         ,"       ,"/270             "Yes, we are|,"| says      1  270   
299         Of       Of/299        treasure?"\n\n"|Of| course      1  299   
301         ,"       ,"/301           \n\n"Of course|,"| says      1  301   
316         ."       ."/316   And so is playing pirates|."|\n      1  316   
50          !"        !"/50        there is a big box|!"| Sam      7   50   
68          !"        !"/68            \n\n"Good idea|!"| Mia      7   68   
79          ."        ."/79        's go inside the box|."|\n      7   79   
131         !"       !"/131        \n"Hello, neighbor|!"| Sam      7  131   
143         ?"       ?"/143        Do you want some tea|?"|\n      7  143   
150         !"       !"/150            \n"Yes, please|!"| Mia      7  150   
160         ."       ."/160       And some cookies, too|."|\n      7  160   
219         ?"       ?"/219        Mia, where are you|?"| she      7  219   
227          ,        ,/227                 .\n\n"Here|,| mom      7  227   
229         !"       !"/229              \n"Here, mom|!"| Sam      7  229   
232          .        ./232            , mom!" Sam says|.| He      7  232   
255         ?"       ?"/255           \n"Are you okay|?"| she      7  255   
268         ."       ."/268        cold and windy today|."|\n      7  268   
277         !"       !"/277          We are fine, mom|!"| Sam      7  277   
291         ."       ."/291           . It is our house|."|\n      7  291   
324         ,"       ,"/324    That is a nice shelter|,"| she      7  324   
48          !"        !"/48           "Look, a snake|!"| Lily      9   48   

     label      loss  max_idx_pos max_idx_tok  max_idx_tok_value  ...  \
88    1/88  0.892003           32        them           0.060124  ...   
153  1/153  0.963728           90        says           0.777926  ...   
156  1/156  0.173373          128          is           0.051997  ...   
170  1/170  0.757954          111          \n           0.216574  ...   
178  1/178  0.096985          155        says           0.531703  ...   
196  1/196  0.142160          172          \n           0.286551  ...   
246  1/246  0.016797          155        says           0.380723  ...   
262  1/262  0.295246          172          \n           0.157250  ...   
268  1/268  0.020565          247          !"           0.122394  ...   
270  1/270  0.622071          248        says           0.257907  ...   
299  1/299  0.522811          248        says           0.070347  ...   
301  1/301  0.381187          272        says           0.300536  ...   
316  1/316  0.441424          264          \n           0.111000  ...   
50    7/50  0.450555            6           .           0.152457  ...   
68    7/68  0.161331           54           .           0.205982  ...   
79    7/79  1.375313           54           .           0.095535  ...   
131  7/131  0.536664           54           .           0.092762  ...   
143  7/143  0.236696           81          \n           0.147158  ...   
150  7/150  0.051303           72           .           0.067307  ...   
160  7/160  0.574495          145          \n           0.122608  ...   
219  7/219  0.039801          154           .           0.084192  ...   
227  7/227

In [57]:
df[df.top_k_features.apply(lambda x: (1669 in x) or (3489 in x))].head(30)

str_tokens unique_token                             context  batch  pos  \
88          !"        !"/88                 .\n\n"Stop|!"| says      1   88   
109         ."       ."/109   friends. They work together|."|\n      1  109   
153         !"       !"/153                 .\n\n"Look|!"| says      1  153   
156          .        ./156              "Look!" says Sara|.| "      1  156   
170         ."       ."/170       is part of the treasure|."|\n      1  170   
178         ,"       ,"/178       "Maybe you are right|,"| says      1  178   
196         ."       ."/196             the star is on it|."|\n      1  196   
246         !"       !"/246                  .\n\n"Wow|!"| says      1  246   
262         ."       ."/262     are the best pirates ever|."|\n      1  262   
268         we       we/268                  \n\n"Yes,| we| are      1  268   
270         ,"       ,"/270               "Yes, we are|,"| says      1  270   
295         ?"       ?"/295     Can we share the treasure|?"|\n      1  295   
299         Of       Of/299          treasure?"\n\n"|Of| course      1  299   
301         ,"       ,"/301             \n\n"Of course|,"| says      1  301   
316         ."       ."/316     And so is playing pirates|."|\n      1  316   
50          !"        !"/50          there is a big box|!"| Sam      7   50   
62          ."        ."/62        make a shelter with it|."|\n      7   62   
68          !"        !"/68              \n\n"Good idea|!"| Mia      7   68   
79          ."        ."/79          's go inside the box|."|\n      7   79   
131         !"       !"/131          \n"Hello, neighbor|!"| Sam      7  131   
143         ?"       ?"/143          Do you want some tea|?"|\n      7  143   
150         !"       !"/150              \n"Yes, please|!"| Mia      7  150   
160         ."       ."/160         And some cookies, too|."|\n      7  160   
219         ?"       ?"/219          Mia, where are you|?"| she      7  219   
227          ,        ,/227                   .\n\n"Here|,| mom      7  227   
229         !"       !"/229                \n"Here, mom|!"| Sam      7  229   
232          .        ./232              , mom!" Sam says|.| He      7  232   
255         ?"       ?"/255             \n"Are you okay|?"| she      7  255   
268         ."       ."/268          cold and windy today|."|\n      7  268   
277         !"       !"/277            We are fine, mom|!"| Sam      7  277   

     label      loss  max_idx_pos max_idx_tok  max_idx_tok_value  ...  \
88    1/88  0.892003           32        them           0.060124  ...   
109  1/109  1.986598           90        says           0.249100  ...   
153  1/153  0.963728           90        says           0.777926  ...   
156  1/156  0.173373          128          is           0.051997  ...   
170  1/170  0.757954          111          \n           0.216574  ...   
178  1/178  0.096985          155        says           0.531703  ...   
196  1/196  0.142160          172          \n           0.286551  ...   
246  1/246  0.016797          155        says           0.380723  ...   
262  1/262  0.295246          172          \n           0.157250  ...   
268  1/268  0.020565          247          !"           0.122394  ...   
270  1/270  0.622071          248        says           0.257907  ...   
295  1/295  0.199696          264          \n           0.127764  ...   
299  1/299  0.522811          248        says           0.070347  ...   
301  1/301  0.381187          272        says           0.300536  ...   
316  1/316  0.441424          264          \n           0.111000  ...   
50    7/50  0.450555            6           .           0.152457  ...   
62    7/62  0.685454           54           .           0.143540  ...   
68    7/68  0.161331           54           .           0.205982  ...   
79    7/79  1.375313           54           .           0.095535  ...   
131  7/131  0.536664           54           .           0.092762  ...   
143  7/143  0.236696 

In [53]:
df['tmp_key'] = df.index  
df_exploded_acts = df.explode('top_k_feature_acts')
df_exploded_features = df.explode('top_k_features')
feature_wise_df = pd.merge(df_exploded_acts, df_exploded_features, left_on='tmp_key', right_on='tmp_key', suffixes=('_acts', '_features'))
feature_wise_df = feature_wise_df.drop(columns=['tmp_key', 'top_k_feature_acts_features', 'top_k_features_acts'])


In [56]:
feature_wise_df[feature_wise_df.top_k_features_features.isin([1669,3489])].sort_values("top_k_feature_acts_acts", ascending=False).head(10).style.background_gradient(cmap="Blues")

## Static Analysis of features

# Feature Dashboards

In [186]:
from importlib import reload
from sae_analysis.visualizer import data_fns
from sae_analysis.visualizer.data_fns import FeatureData
from typing import Dict
reload(data_fns)


os.environ["TOKENIZERS_PARALLELISM"] = "false"
dataset="roneneldan/TinyStories"
train_dataset = load_dataset(dataset, split="train[:3%]")
tokenized_data = utils.tokenize_and_concatenate(train_dataset, model.tokenizer, max_length=128)
tokenized_data = tokenized_data.shuffle(42)
all_tokens = tokenized_data["tokens"]


# Currently, don't think much more time can be squeezed out of it. Maybe the best saving would be to
# make the entire sequence indexing parallelized, but that's possibly not worth it right now.

max_batch_size = 32
total_batch_size = 512 * 50
feature_idx = token_df.tail(1).top_k_features.values[0]
# max_batch_size = 512
# total_batch_size = 16384
# feature_idx = list(range(1000))

tokens = all_tokens[:total_batch_size]

feature_data: Dict[int, FeatureData] = data_fns.get_feature_data(
    encoder=sparse_autoencoder,
    # encoder_B=sparse_autoencoder,
    model=model,
    hook_point=sparse_autoencoder.cfg.hook_point,
    hook_point_layer=sparse_autoencoder.cfg.hook_point_layer - 1,
    hook_point_head_index=sparse_autoencoder.cfg.hook_point_head_index,
    tokens=tokens,
    feature_idx=feature_idx,
    max_batch_size=max_batch_size,
    left_hand_k = 3,
    buffer = (5, 5),
    n_groups = 10,
    first_group_size = 20,
    other_groups_size = 5,
    verbose = True,
)




Storing model activations: 100%|██████████| 800/800 [00:31<00:00, 25.09it/s]


        Time taken for each task         
┏━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━┳━━━━━━━┓
┃ Task                 ┃ Time   ┃ Pct % ┃
┡━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━╇━━━━━━━┩
│ Setup code           │ 0.17s  │ 0.5%  │
│ Fwd passes           │ 31.89s │ 86.7% │
│ Concats              │ 0.03s  │ 0.1%  │
│ Left-hand tables     │ 0.65s  │ 1.8%  │
│ Right-hand sequences │ 4.05s  │ 11.0% │
│ Middle column        │ 0.73s  │ 2.0%  │
└──────────────────────┴────────┴───────┘

Estimated time for all 4096 features = 65 minutes



In [191]:
del feature_data
torch.mps.empty_cache()

In [189]:
for test_idx in feature_idx:
    html_str = feature_data[test_idx].get_all_html()
    path = f"tiny_stories_features/{test_idx:04}.html"
    print(f"Saving to {path}")
    with open(path, "w") as f:
        f.write(html_str)

Saving to tiny_stories_features/3489.html
Saving to tiny_stories_features/1669.html
Saving to tiny_stories_features/1401.html
Saving to tiny_stories_features/3629.html
Saving to tiny_stories_features/1352.html
Saving to tiny_stories_features/2393.html
Saving to tiny_stories_features/0995.html
Saving to tiny_stories_features/3258.html
Saving to tiny_stories_features/2455.html
Saving to tiny_stories_features/1607.html
